In [1]:
from utils import *
warnings.filterwarnings('ignore')
%matplotlib inline
from sklearn.decomposition import PCA

In [2]:
fd_collection = getCollection("team_5_mwdb_phase_2", "fd_collection")

In [3]:
selected_feature_model = "fc_fd"

t = int(input("Enter value of t: "))
if t < 1:
    raise ValueError("t should be a positive integer")

num_layers = int(input("Enter the number of layers: "))
if num_layers < 1:
    raise ValueError("num_layers should be a positive integer")

num_hashes_per_layer = int(input("Enter the number of hashes per layer: "))
if num_hashes_per_layer < 1:
    raise ValueError("num_hashes_per_layer should be a positive integer")

In [4]:
all_images = list(fd_collection.find())
all_images = sorted(all_images, key = lambda x: x["image_id"])

odd_image_ids = [img["image_id"] for img in all_images if img["image_id"] % 2 == 0]

even_image_labels = [img["true_label"] for img in all_images if img["image_id"] % 2 == 0]
odd_image_labels = [img["true_label"] for img in all_images if img["image_id"] % 2 != 0]

feature_vectors = [np.array(img[selected_feature_model]).flatten() for img in all_images]

total_len = len(feature_vectors)
even_feature_vectors = []
odd_feature_vectors = []

for i in range(total_len):
  if i % 2 == 0:
    even_feature_vectors.append(feature_vectors[i])
  else:
    odd_feature_vectors.append(feature_vectors[i])

even_feature_vectors = np.array(even_feature_vectors)
odd_feature_vectors = np.array(odd_feature_vectors)

odd_len = odd_feature_vectors.shape[0]
even_len = even_feature_vectors.shape[0]

In [21]:
query_image_id = int(input("Enter value of query_image_id: "))
if query_image_id < 1:
    raise ValueError("query_image_id should be a positive integer")

num_vectors = even_feature_vectors.shape[0]
vector_dimension = even_feature_vectors.shape[1]

lsh = LSHIndex(num_layers, num_hashes_per_layer, vector_dimension)

for index, vector in enumerate(even_feature_vectors):
    lsh.add_vector(vector.tolist(), index * 2)

query_vector = np.array(odd_feature_vectors[(query_image_id // 2)])

result_t_unique, unique_count, overall_count = lsh.query_t_unique(query_vector, t)
print(f"Number of unique vectors considered: {unique_count}")
print(f"Overall number of vectors considered: {overall_count}")
print(f"{t} Most Similar Vectors:")
print(f"Label of the input image: {odd_image_labels[(query_image_id // 2)]}")

training_vectors = []
training_labels = []
for result in result_t_unique:
    training_labels.append(even_image_labels[(result[0] // 2)])
    training_vectors.append(result[1])
    print(f"Label: {even_image_labels[(result[0] // 2)]}, {result}")

Number of unique vectors considered: 210
Overall number of vectors considered: 265
15 Most Similar Vectors:
Label of the input image: 5
Label: 3, (1078, [-0.09339900314807892, -0.003246128559112549, 0.008638394996523857, -0.19130085408687592, -0.09068502485752106, 0.0852460116147995, 0.1705757975578308, -0.19062790274620056, 0.11604724824428558, -0.1439134180545807, -0.03672311082482338, -0.012472901493310928, -0.20803089439868927, -0.19453124701976776, -0.08260566741228104, -0.10372554510831833, 0.2793111205101013, 0.036157600581645966, 0.01458636112511158, -0.29630789160728455, 0.4764160215854645, -0.3228815793991089, -0.370932012796402, -0.031474385410547256, -0.2118302881717682, -0.19923610985279083, -0.196367546916008, 0.07233747839927673, 0.06497518718242645, -0.15095970034599304, -0.1327892243862152, -0.07300391793251038, 0.020353320986032486, -0.09443800151348114, 0.058752235025167465, 0.24090096354484558, -0.4528697729110718, -0.17242345213890076, 0.3063212037086487, -0.005360

In [25]:
print(training_vectors)
print(training_labels)

user_feedback = []

length = len(training_labels)

for i in range(length):
  print(f"Label: {training_labels[i]}, vector: {training_vectors[i]}")
  feedback = input("What is the feedback for result 1? (R+, R, I, I-)")

  match feedback:

    case "R+":
      user_feedback.append(2)

    case "R":
      user_feedback.append(1)

    case "I":
      user_feedback.append(-1)

    case "I-":
      user_feedback.append(-2)

[[-0.09339900314807892, -0.003246128559112549, 0.008638394996523857, -0.19130085408687592, -0.09068502485752106, 0.0852460116147995, 0.1705757975578308, -0.19062790274620056, 0.11604724824428558, -0.1439134180545807, -0.03672311082482338, -0.012472901493310928, -0.20803089439868927, -0.19453124701976776, -0.08260566741228104, -0.10372554510831833, 0.2793111205101013, 0.036157600581645966, 0.01458636112511158, -0.29630789160728455, 0.4764160215854645, -0.3228815793991089, -0.370932012796402, -0.031474385410547256, -0.2118302881717682, -0.19923610985279083, -0.196367546916008, 0.07233747839927673, 0.06497518718242645, -0.15095970034599304, -0.1327892243862152, -0.07300391793251038, 0.020353320986032486, -0.09443800151348114, 0.058752235025167465, 0.24090096354484558, -0.4528697729110718, -0.17242345213890076, 0.3063212037086487, -0.005360260605812073, 0.223260760307312, -0.13058391213417053, 0.11432977020740509, -0.013286445289850235, 0.11295782774686813, -0.13005197048187256, -0.0814252

In [26]:
print(user_feedback)

[-2, -1, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2]
